# Project 2: Breakout Strategy
## Instructions
Each problem consists of a function to implement and instructions on how to implement the function.  The parts of the function that need to be implemented are marked with a `# TODO` comment. After implementing the function, run the cell to test it against the unit tests we've provided. For each problem, we provide one or more unit tests from our `project_tests` package. These unit tests won't tell you if your answer is correct, but will warn you of any major errors. Your code will be checked for the correct solution when you submit it to Udacity.

## Packages
When you implement the functions, you'll only need to you use the packages you've used in the classroom, like [Pandas](https://pandas.pydata.org/) and [Numpy](http://www.numpy.org/). These packages will be imported for you. We recommend you don't add any import statements, otherwise the grader might not be able to run your code.

The other packages that we're importing are `helper`, `project_helper`, and `project_tests`. These are custom packages built to help you solve the problems.  The `helper` and `project_helper` module contains utility functions and graph functions. The `project_tests` contains the unit tests for all the problems.


### Load Packages

In [7]:
import pandas as pd
import numpy as np
import helper
import project_helper
import project_tests

## Market Data
### Load Data
While using real data will give you hands on experience, it's doesn't cover all the topics we try to condense in one project. We'll solve this by creating new stocks. We've create a scenario where companies mining [Terbium](https://en.wikipedia.org/wiki/Terbium) are making huge profits. All the companies in this sector of the market are made up. They represent a sector with large growth that will be used for demonstration latter in this project.

In [8]:
df_original = pd.read_csv('eod-quotemedia.csv', parse_dates=['date'], index_col=False)

# Add TB sector to the market
df = df_original
df = pd.concat([df] + project_helper.generate_tb_sector(df[df['ticker'] == 'AAPL']['date']), ignore_index=True)

close = df.reset_index().pivot(index='date', columns='ticker', values='adj_close')
high = df.reset_index().pivot(index='date', columns='ticker', values='adj_high')
low = df.reset_index().pivot(index='date', columns='ticker', values='adj_low')

print('Loaded Data')

Loaded Data


### View Data
To see what one of these 2-d matrices looks like, let's take a look at the closing prices matrix.

In [9]:
close.head(15)

ticker               A         AAL         AAP        AAPL        ABBV  \
date                                                                     
2013-07-01 29.99418563 16.17609308 81.13821681 53.10917319 34.92447839   
2013-07-02 29.65013670 15.81983388 80.72207258 54.31224742 35.42807578   
2013-07-03 29.70518453 16.12794994 81.23729877 54.61204262 35.44486235   
2013-07-05 30.43456826 16.21460758 81.82188233 54.17338125 35.85613355   
2013-07-08 30.52402098 16.31089385 82.95141667 53.86579916 36.66188936   
2013-07-09 30.68916447 16.71529618 82.43619048 54.81320389 36.35973093   
2013-07-10 31.17771395 16.53235227 81.99032166 54.60295791 36.85493502   
2013-07-11 31.45983407 16.72492481 82.00022986 55.45406479 37.08155384   
2013-07-12 31.48047700 16.90786872 81.91105609 55.35309481 38.15724076   
2013-07-15 31.72819223 17.10044125 82.61453801 55.47379158 37.79303181   
2013-07-16 31.59057266 17.28338516 81.62371841 55.83133953 37.10696377   
2013-07-17 31.38414330 17.76481650 80.74188897 55.84626440 37.23401341   
2013-07-18 31.58369168 17.73593062 81.74261676 56.03418797 37.53893253   
2013-07-19 31.79012104 17.55298671 81.45527908 55.15063572 37.70833205   
2013-07-22 32.20297975 17.47595770 81.99032166 55.32713852 38.08948096   

ticker             ABC         ABT         ACN        ADBE         ADI  \
date                                                                     
2013-07-01 50.86319750 31.42538772 64.69409505 46.23500000 39.91336014   
2013-07-02 50.69676639 31.27288084 64.71204071 46.03000000 39.86057632   
2013-07-03 50.93716689 30.72565028 65.21451912 46.42000000 40.18607651   
2013-07-05 51.37173702 31.32670680 66.07591068 47.00000000 40.65233352   
2013-07-08 52.03746147 31.76628544 66.82065546 46.62500000 40.25645492   
2013-07-09 51.69535307 31.16522893 66.48866080 47.26000000 40.69632003   
2013-07-10 52.28710814 31.16522893 66.71298151 47.25000000 41.10979324   
2013-07-11 53.72026495 31.85599537 67.47567196 47.99000000 42.22705062   
2013-07-12 53.98840397 31.81096287 67.76280247 48.39000000 42.53495620   
2013-07-15 53.84971137 31.95506689 68.41781897 48.12000000 42.57894271   
2013-07-16 53.88669607 32.15320992 67.55642741 47.48500000 42.68451033   
2013-07-17 54.06237335 32.26128793 67.43978064 48.04000000 42.80767257   
2013-07-18 53.91443458 32.15320992 67.69101984 48.19000000 42.52615889   
2013-07-19 54.37674323 32.30632044 67.49361761 48.07000000 42.20945601   
2013-07-22 54.54317435 32.24327493 67.29621538 48.28000000 42.17426681   

ticker         ...              XL        XLNX         XOM        XRAY  \
date           ...                                                       
2013-07-01     ...     27.66879066 35.28892781 76.32080247 40.02387348   
2013-07-02     ...     27.54228410 35.05903252 76.60816761 39.96552964   
2013-07-03     ...     27.33445191 35.28008569 76.65042719 40.00442554   
2013-07-05     ...     27.69589920 35.80177117 77.39419581 40.67537968   
2013-07-08     ...     27.98505704 35.20050655 77.96892611 40.64620776   
2013-07-09     ...     28.31939579 35.50113886 78.89018496 40.80179133   
2013-07-10     ...     27.95794850 36.39419366 78.45068533 40.71427558   
2013-07-11     ...     28.50011944 37.00430040 78.83102155 41.01571874   
2013-07-12     ...     28.92482002 38.00346072 78.94089646 40.83096325   
2013-07-15     ...     29.27723113 38.17146113 78.81411772 40.84068723   
2013-07-16     ...     29.04229039 38.27314559 78.85637730 40.86013517   
2013-07-17     ...     29.18686931 38.48977769 78.99160796 40.93792696   
2013-07-18     ...     29.55735279 40.52346684 79.76918424 41.22964615   
2013-07-19     ...     29.71096789 40.54999322 80.43688561 41.24909410   
2013-07-22     ...     29.84651063 40.59420386 80.14952046 41.49219343   

ticker             XRX         XYL         YUM         ZBH        ZION  \
date                                                                     
2013-07-01 22.10666494 25.75338607 45.48038323 71.89882693 27.85858718   
2

### Stock Example
Let's see what a single stock looks like from the closing prices. For this example and future display examples in this project, we'll use Apple's stock (AAPL). If we tried to graph all the stocks, it would be too much information.

In [10]:
apple_ticker = 'AAPL'
project_helper.plot_stock(close[apple_ticker], '{} Stock'.format(apple_ticker))

## The Alpha Research Process

In this project you will code and evaluate a "breakout" signal. It is important to understand where these steps fit in the alpha research workflow. The signal-to-noise ratio in trading signals is very low and, as such, it is very easy to fall into the trap of _overfitting_ to noise. It is therefore inadvisable to jump right into signal coding. To help mitigate overfitting, it is best to start with a general observation and hypothesis; i.e., you should be able to answer the following question _before_ you touch any data:

> What feature of markets or investor behaviour would lead to a persistent anomaly that my signal will try to use?

Ideally the assumptions behind the hypothesis will be testable _before_ you actually code and evaluate the signal itself. The workflow therefore is as follows:

![image](images/alpha_steps.png)

In this project, we assume that the first three steps area done ("observe & research", "form hypothesis", "validate hypothesis"). The hypothesis you'll be using for this project is the following:
- In the absence of news or significant investor trading interest, stocks oscillate in a range.
- Traders seek to capitalize on this range-bound behaviour periodically by selling/shorting at the top of the range and buying/covering at the bottom of the range. This behaviour reinforces the existence of the range.
- When stocks break out of the range, due to, e.g., a significant news release or from market pressure from a large investor:
    - the liquidity traders who have been providing liquidity at the bounds of the range seek to cover their positions to mitigate losses, thus magnifying the move out of the range, _and_
    - the move out of the range attracts other investor interest; these investors, due to the behavioural bias of _herding_ (e.g., [Herd Behavior](https://www.investopedia.com/university/behavioral_finance/behavioral8.asp)) build positions which favor continuation of the trend.


Using this hypothesis, let start coding..
## Compute the Highs and Lows in a Window
You'll use the price highs and lows as an indicator for the breakout strategy. In this section, implement `get_high_lows_lookback` to get the maximum high price and minimum low price over a window of days. The variable `lookback_days` contains the number of days to look in the past. Make sure this doesn't include the current day.

In [15]:
close.shift().head(10)

ticker               A         AAL         AAP        AAPL        ABBV  \
date                                                                     
2013-07-01         nan         nan         nan         nan         nan   
2013-07-02 29.99418563 16.17609308 81.13821681 53.10917319 34.92447839   
2013-07-03 29.65013670 15.81983388 80.72207258 54.31224742 35.42807578   
2013-07-05 29.70518453 16.12794994 81.23729877 54.61204262 35.44486235   
2013-07-08 30.43456826 16.21460758 81.82188233 54.17338125 35.85613355   
2013-07-09 30.52402098 16.31089385 82.95141667 53.86579916 36.66188936   
2013-07-10 30.68916447 16.71529618 82.43619048 54.81320389 36.35973093   
2013-07-11 31.17771395 16.53235227 81.99032166 54.60295791 36.85493502   
2013-07-12 31.45983407 16.72492481 82.00022986 55.45406479 37.08155384   
2013-07-15 31.48047700 16.90786872 81.91105609 55.35309481 38.15724076   

ticker             ABC         ABT         ACN        ADBE         ADI  \
date                                                                     
2013-07-01         nan         nan         nan         nan         nan   
2013-07-02 50.86319750 31.42538772 64.69409505 46.23500000 39.91336014   
2013-07-03 50.69676639 31.27288084 64.71204071 46.03000000 39.86057632   
2013-07-05 50.93716689 30.72565028 65.21451912 46.42000000 40.18607651   
2013-07-08 51.37173702 31.32670680 66.07591068 47.00000000 40.65233352   
2013-07-09 52.03746147 31.76628544 66.82065546 46.62500000 40.25645492   
2013-07-10 51.69535307 31.16522893 66.48866080 47.26000000 40.69632003   
2013-07-11 52.28710814 31.16522893 66.71298151 47.25000000 41.10979324   
2013-07-12 53.72026495 31.85599537 67.47567196 47.99000000 42.22705062   
2013-07-15 53.98840397 31.81096287 67.76280247 48.39000000 42.53495620   

ticker         ...              XL        XLNX         XOM        XRAY  \
date           ...                                                       
2013-07-01     ...             nan         nan         nan         nan   
2013-07-02     ...     27.66879066 35.28892781 76.32080247 40.02387348   
2013-07-03     ...     27.54228410 35.05903252 76.60816761 39.96552964   
2013-07-05     ...     27.33445191 35.28008569 76.65042719 40.00442554   
2013-07-08     ...     27.69589920 35.80177117 77.39419581 40.67537968   
2013-07-09     ...     27.98505704 35.20050655 77.96892611 40.64620776   
2013-07-10     ...     28.31939579 35.50113886 78.89018496 40.80179133   
2013-07-11     ...     27.95794850 36.39419366 78.45068533 40.71427558   
2013-07-12     ...     28.50011944 37.00430040 78.83102155 41.01571874   
2013-07-15     ...     28.92482002 38.00346072 78.94089646 40.83096325   

ticker             XRX         XYL         YUM         ZBH        ZION  \
date                                                                     
2013-07-01         nan         nan         nan         nan         nan   
2013-07-02 22.10666494 25.75338607 45.48038323 71.89882693 27.85858718   
2013-07-03 22.08273998 25.61367511 45.40266113 72.93417195 28.03893238   
2013-07-05 22.20236479 25.73475794 46.06329899 72.30145844 28.18131017   
2013-07-08 22.58516418 26.06075017 46.41304845 73.16424628 29.39626730   
2013-07-09 22.48946433 26.22840332 46.95062632 73.89282298 29.57661249   
2013-07-10 22.48946433 26.58233774 47.28094525 73.70108798 28.91218282   
2013-07-11 22.96796358 26.98284247 47.08340158 74.00785631 28.32368796   
2013-07-12 23.23113816 27.03872686 46.54333492 74.93774876 27.84909533   
2013-07-15 23.49431274 27.08529718 45.96422730 75.68549560 28.44708204   

ticker             ZTS  
date                    
2013-07-01         nan  
2013-07-02 29.44789315  
2013-07-03 28.57244125  
2013-07-05 28.16838652  
2013-07-08 29.02459772  
2013-07-09 29.76536472  
2013-07-10 29.80384612  
2013-07-11 29.86156823  
2013-07-12 29.74612402  
2013-07-15 30.15979909  

[10 rows x 519 columns]

**high와 low DataFrame에서 오늘 날짜가 포함되지 않도록 ```.shift()```로 오늘치 값을 뒤로 밀어버린 뒤 ```rolling()```시켜서 각각 max와 min값을 뽑도록 함수 작성**

### View Data
Let's use your implementation of `get_high_lows_lookback` to get the highs and lows for the past 50 days and compare it to it their respective stock.  Just like last time, we'll use Apple's stock as the example to look at.

In [12]:
lookback_days = 50
lookback_high, lookback_low = get_high_lows_lookback(high, low, lookback_days)
project_helper.plot_high_low(
    close[apple_ticker],
    lookback_high[apple_ticker],
    lookback_low[apple_ticker],
    'High and Low of {} Stock'.format(apple_ticker))

## Compute Long and Short Signals
Using the generated indicator of highs and lows, create long and short signals using a breakout strategy. Implement `get_long_short` to generate the following signals:

| Signal | Condition |
|----|------|
| -1 | Low > Close Price |
| 1  | High < Close Price |
| 0  | Otherwise |

In this chart, **Close Price** is the `close` parameter. **Low** and **High** are the values generated from `get_high_lows_lookback`, the `lookback_high` and `lookback_low` parameters.

In [13]:
def get_long_short(close, lookback_high, lookback_low):
    """
    Generate the signals long, short, and do nothing.
    
    Parameters
    ----------
    close : DataFrame
        Close price for each ticker and date
    lookback_high : DataFrame
        Lookback high price for each ticker and date
    lookback_low : DataFrame
        Lookback low price for each ticker and date
    
    Returns
    -------
    long_short : DataFrame
        The long, short, and do nothing signals for each ticker and date
    """
    #TODO: Implement function
    long_short = pd.DataFrame(0, index=close.index, columns=close.columns)
    long_short[close > lookback_high] = 1
    long_short[close < lookback_low] = -1
    
    return long_short

project_tests.test_get_long_short(get_long_short)

Tests Passed


**모든 값이 0을 갖는 DF 생성 후, 조건에 따라 종가가 lookback_high보다 크면 1의 값을, lookback_low보다 작으면 -1을 갖도록 함수 작성**

### View Data
Let's compare the signals you generated against the close prices. This chart will show a lot of signals. Too many in fact. We'll talk about filtering the redundant signals in the next problem. 

In [16]:
signal = get_long_short(close, lookback_high, lookback_low)
project_helper.plot_signal(
    close[apple_ticker],
    signal[apple_ticker],
    'Long and Short of {} Stock'.format(apple_ticker))

## Filter Signals
That was a lot of repeated signals! If we're already shorting a stock, having an additional signal to short a stock isn't helpful for this strategy. This also applies to additional long signals when the last signal was long.

Implement `filter_signals` to filter out repeated long or short signals within the `lookahead_days`. If the previous signal was the same, change the signal to `0` (do nothing signal). For example, say you have a single stock time series that is

`[1, 0, 1, 0, 1, 0, -1, -1]`

Running `filter_signals` with a lookahead of 3 days should turn those signals into

`[1, 0, 0, 0, 1, 0, -1, 0]`

To help you implement the function, we have provided you with the `clear_signals` function. This will remove all signals within a window after the last signal. For example, say you're using a windows size of 3 with `clear_signals`. It would turn the Series of long signals

`[0, 1, 0, 0, 1, 1, 0, 1, 0]`

into

`[0, 1, 0, 0, 0, 1, 0, 0, 0]`

`clear_signals` only takes a Series of the same type of signals, where `1` is the signal and `0` is no signal. It can't take a mix of long and short signals. Using this function, implement `filter_signals`. 

For implementing `filter_signals`, we don't reccommend you try to find a vectorized solution. Instead, you should use the [`iterrows`](https://pandas.pydata.org/pandas-docs/version/0.21/generated/pandas.DataFrame.iterrows.html) over each column.

In [42]:
a = pd.DataFrame([1, 0, 0, -1, -1, 1, 1, 0])
a[a!=1].fillna(0)

0
0  0.00000000
1  0.00000000
2  0.00000000
3 -1.00000000
4 -1.00000000
5  0.00000000
6  0.00000000
7  0.00000000

In [47]:
def clear_signals(signals, window_size):
    """
    Clear out signals in a Series of just long or short signals.
    
    Remove the number of signals down to 1 within the window size time period.
    
    Parameters
    ----------
    signals : Pandas Series
        The long, short, or do nothing signals
    window_size : int
        The number of days to have a single signal       
    
    Returns
    -------
    signals : Pandas Series
        Signals with the signals removed from the window size
    """
    # Start with buffer of window size
    # This handles the edge case of calculating past_signal in the beginning
    clean_signals = [0]*window_size
    
    for signal_i, current_signal in enumerate(signals):
        # Check if there was a signal in the past window_size of days
        has_past_signal = bool(sum(clean_signals[signal_i:signal_i+window_size]))
        # Use the current signal if there's no past signal, else 0/False
        clean_signals.append(not has_past_signal and current_signal)
        
    # Remove buffer
    clean_signals = clean_signals[window_size:]

    # Return the signals as a Series of Ints
    return pd.Series(np.array(clean_signals).astype(np.int), signals.index)


def filter_signals(signal, lookahead_days):
    """
    Filter out signals in a DataFrame.
    
    Parameters
    ----------
    signal : DataFrame
        The long, short, and do nothing signals for each ticker and date
    lookahead_days : int
        The number of days to look ahead
    
    Returns
    -------
    filtered_signal : DataFrame
        The filtered long, short, and do nothing signals for each ticker and date
    """
    #TODO: Implement function
    short_signal = signal[signal != 1].fillna(0).astype('int64').T
    for i, row in short_signal.iterrows():
        short_signal.loc[i] = clear_signals(short_signal.loc[i], lookahead_days)
    
    long_signal = signal[signal != -1].fillna(0).astype('int64').T
    for i, row in long_signal.iterrows():
        long_signal.loc[i] = clear_signals(long_signal.loc[i], lookahead_days)
    
    filtered_signal = long_signal.T + short_signal.T
    
    return filtered_signal

project_tests.test_filter_signals(filter_signals)

Tests Passed


**```clear_signals()```함수가 서로 다른 포지션을 한꺼번에 처리할 수가 없기 때문에 short position, long_position을 갖는 DataFrame을 각각 생성 후,<br>
for loop을 통해 각각에다가 clear_signals를 적용한 뒤, 두 DF를 합친 filtered_signal DF를 생성하는 함수**

### View Data
Let's view the same chart as before, but with the redundant signals removed.

In [48]:
signal_5 = filter_signals(signal, 5)
signal_10 = filter_signals(signal, 10)
signal_20 = filter_signals(signal, 20)
for signal_data, signal_days in [(signal_5, 5), (signal_10, 10), (signal_20, 20)]:
    project_helper.plot_signal(
        close[apple_ticker],
        signal_data[apple_ticker],
        'Long and Short of {} Stock with {} day signal window'.format(apple_ticker, signal_days))

## Lookahead Close Prices
With the trading signal done, we can start working on evaluating how many days to short or long the stocks. In this problem, implement `get_lookahead_prices` to get the close price days ahead in time. You can get the number of days from the variable `lookahead_days`. We'll use the lookahead prices to calculate future returns in another problem.

In [53]:
def get_lookahead_prices(close, lookahead_days):
    """
    Get the lookahead prices for `lookahead_days` number of days.
    
    Parameters
    ----------
    close : DataFrame
        Close price for each ticker and date
    lookahead_days : int
        The number of days to look ahead
    
    Returns
    -------
    lookahead_prices : DataFrame
        The lookahead prices for each ticker and date
    """
    #TODO: Implement function
    lookahead_prices = close.shift(-lookahead_days)
    return lookahead_prices

project_tests.test_get_lookahead_prices(get_lookahead_prices)

Tests Passed


### View Data
Using the `get_lookahead_prices` function, let's generate lookahead closing prices for 5, 10, and 20 days.

Let's also chart a subsection of a few months of the Apple stock instead of years. This will allow you to view the differences between the 5, 10, and 20 day lookaheads. Otherwise, they will mesh together when looking at a chart that is zoomed out.

In [54]:
lookahead_5 = get_lookahead_prices(close, 5)
lookahead_10 = get_lookahead_prices(close, 10)
lookahead_20 = get_lookahead_prices(close, 20)
project_helper.plot_lookahead_prices(
    close[apple_ticker].iloc[150:250],
    [
        (lookahead_5[apple_ticker].iloc[150:250], 5),
        (lookahead_10[apple_ticker].iloc[150:250], 10),
        (lookahead_20[apple_ticker].iloc[150:250], 20)],
    '5, 10, and 20 day Lookahead Prices for Slice of {} Stock'.format(apple_ticker))

## Lookahead Price Returns
Implement `get_return_lookahead` to generate the log price return between the closing price and the lookahead price.

In [60]:
def get_return_lookahead(close, lookahead_prices):
    """
    Calculate the log returns from the lookahead days to the signal day.
    
    Parameters
    ----------
    close : DataFrame
        Close price for each ticker and date
    lookahead_prices : DataFrame
        The lookahead prices for each ticker and date
    
    Returns
    -------
    lookahead_returns : DataFrame
        The lookahead log returns for each ticker and date
    """
    #TODO: Implement function
    lookahead_returns = np.log(lookahead_prices/close)
    return lookahead_returns

project_tests.test_get_return_lookahead(get_return_lookahead)

Tests Passed


### View Data
Using the same lookahead prices and same subsection of the Apple stock from the previous problem, we'll view the lookahead returns.

In order to view price returns on the same chart as the stock, a second y-axis will be added. When viewing this chart, the axis for the price of the stock will be on the left side, like previous charts. The axis for price returns will be located on the right side.

In [61]:
price_return_5 = get_return_lookahead(close, lookahead_5)
price_return_10 = get_return_lookahead(close, lookahead_10)
price_return_20 = get_return_lookahead(close, lookahead_20)
project_helper.plot_price_returns(
    close[apple_ticker].iloc[150:250],
    [
        (price_return_5[apple_ticker].iloc[150:250], 5),
        (price_return_10[apple_ticker].iloc[150:250], 10),
        (price_return_20[apple_ticker].iloc[150:250], 20)],
    '5, 10, and 20 day Lookahead Returns for Slice {} Stock'.format(apple_ticker))

## Compute the Signal Return
Using the price returns generate the signal returns.

In [62]:
def get_signal_return(signal, lookahead_returns):
    """
    Compute the signal returns.
    
    Parameters
    ----------
    signal : DataFrame
        The long, short, and do nothing signals for each ticker and date
    lookahead_returns : DataFrame
        The lookahead log returns for each ticker and date
    
    Returns
    -------
    signal_return : DataFrame
        Signal returns for each ticker and date
    """
    #TODO: Implement function
    signal_return = signal * lookahead_returns
    return signal_return

project_tests.test_get_signal_return(get_signal_return)

Tests Passed


### View Data
Let's continue using the previous lookahead prices to view the signal returns. Just like before, the axis for the signal returns is on the right side of the chart.

In [63]:
title_string = '{} day LookaheadSignal Returns for {} Stock'
signal_return_5 = get_signal_return(signal_5, price_return_5)
signal_return_10 = get_signal_return(signal_10, price_return_10)
signal_return_20 = get_signal_return(signal_20, price_return_20)
project_helper.plot_signal_returns(
    close[apple_ticker],
    [
        (signal_return_5[apple_ticker], signal_5[apple_ticker], 5),
        (signal_return_10[apple_ticker], signal_10[apple_ticker], 10),
        (signal_return_20[apple_ticker], signal_20[apple_ticker], 20)],
    [title_string.format(5, apple_ticker), title_string.format(10, apple_ticker), title_string.format(20, apple_ticker)])

## Test for Significance
### Histogram
Let's plot a histogram of the signal return values.

In [64]:
project_helper.plot_signal_histograms(
    [signal_return_5, signal_return_10, signal_return_20],
    'Signal Return',
    ('5 Days', '10 Days', '20 Days'))

## Outliers
You might have noticed the outliers in the 10 and 20 day histograms. To better visualize the outliers, let's compare the 5, 10, and 20 day signals returns to normal distributions with the same mean and deviation for each signal return distributions.

In [ ]:
project_helper.plot_signal_to_normal_histograms(
    [signal_return_5, signal_return_10, signal_return_20],
    'Signal Return',
    ('5 Days', '10 Days', '20 Days'))

## Kolmogorov-Smirnov Test
While you can see the outliers in the histogram, we need to find the stocks that are causing these outlying returns. We'll use the Kolmogorov-Smirnov Test or KS-Test. This test will be applied to teach ticker's signal returns where a long or short signal exits.

In [65]:
# Filter out returns that don't have a long or short signal.
long_short_signal_returns_5 = signal_return_5[signal_5 != 0].stack()
long_short_signal_returns_10 = signal_return_10[signal_10 != 0].stack()
long_short_signal_returns_20 = signal_return_20[signal_20 != 0].stack()

# Get just ticker and signal return
long_short_signal_returns_5 = long_short_signal_returns_5.reset_index().iloc[:, [1,2]]
long_short_signal_returns_5.columns = ['ticker', 'signal_return']
long_short_signal_returns_10 = long_short_signal_returns_10.reset_index().iloc[:, [1,2]]
long_short_signal_returns_10.columns = ['ticker', 'signal_return']
long_short_signal_returns_20 = long_short_signal_returns_20.reset_index().iloc[:, [1,2]]
long_short_signal_returns_20.columns = ['ticker', 'signal_return']

# View some of the data
long_short_signal_returns_5.head(10)

ticker  signal_return
0       A     0.00732604
1     ABC     0.01639650
2     ADP     0.00981520
3  AGENEN     0.01989183
4    AKAM     0.04400495
5    ALGN     0.01545561
6  ALTAIC     0.02827575
7     APC     0.00305859
8      BA     0.08061297
9  BAKERI     0.02028120

This gives you the data to use in the KS-Test.

Now it's time to implement the function `calculate_kstest` to use Kolmogorov-Smirnov test (KS test) between a normal distribution and each stock's signal returns. Run KS test on a normal distribution against each stock's signal returns. Use [`scipy.stats.kstest`](https://docs.scipy.org/doc/scipy-0.14.0/reference/generated/scipy.stats.kstest.html#scipy-stats-kstest) perform the KS test. When calculating the standard deviation of the signal returns, make sure to set the delta degrees of freedom to 0.

For this function, we don't reccommend you try to find a vectorized solution. Instead, you should iterate over the [`groupby`](https://pandas.pydata.org/pandas-docs/version/0.21/generated/pandas.DataFrame.groupby.html) function.

<br>
<br>

# __Attention__

The return of all stocks follow a whole normal distribution. so the mean and std of your normal args should be the mean and std of all stocks return, but not a single group.

<br>
<br>

In [89]:
for ticker, value in long_short_signal_returns_5.groupby('ticker'):
    print(value['signal_return'])

ValueError: too many values to unpack (expected 2)

In [91]:
long_short_signal_returns_5['signal_return'].mean()

0.005287613417738384

In [95]:
from scipy.stats import kstest


def calculate_kstest(long_short_signal_returns):
    """
    Calculate the KS-Test against the signal returns with a long or short signal.
    
    Parameters
    ----------
    long_short_signal_returns : DataFrame
        The signal returns which have a signal.
        This DataFrame contains two columns, "ticker" and "signal_return"
    
    Returns
    -------
    ks_values : Pandas Series
        KS static for all the tickers
    p_values : Pandas Series
        P value for all the tickers
    """
    #TODO: Implement function
    sample_mean = long_short_signal_returns['signal_return'].mean()
    sample_std = long_short_signal_returns['signal_return'].std(ddof=0)
    ks_values = pd.Series()
    p_values = pd.Series()
    for company, value in long_short_signal_returns.groupby('ticker'):
        ks_values[company] = kstest(value['signal_return'], 'norm', (sample_mean, sample_std))[0]
        p_values[company] = kstest(value['signal_return'], 'norm', (sample_mean, sample_std))[1]
        
    return ks_values, p_values


project_tests.test_calculate_kstest(calculate_kstest)

Tests Passed


### View Data
Using the signal returns we created above, let's calculate the ks and p values.

In [96]:
ks_values_5, p_values_5 = calculate_kstest(long_short_signal_returns_5)
ks_values_10, p_values_10 = calculate_kstest(long_short_signal_returns_10)
ks_values_20, p_values_20 = calculate_kstest(long_short_signal_returns_20)

print('ks_values_5')
print(ks_values_5.head(10))
print('p_values_5')
print(p_values_5.head(10))

ks_values_5
A      0.17215195
AAL    0.10741473
AAP    0.19697881
AAPL   0.15569015
ABBV   0.16818459
ABC    0.21417623
ABT    0.21375064
ACN    0.28224561
ADBE   0.24271084
ADI    0.19432446
dtype: float64
p_values_5
A      0.18704938
AAL    0.72476387
AAP    0.04499485
AAPL   0.24691661
ABBV   0.24672176
ABC    0.02726939
ABT    0.04826683
ACN    0.00584829
ADBE   0.00911163
ADI    0.09877590
dtype: float64


## Find Outliers
With the ks and p values calculate, let's find which symbols are the outliers. Implement the `find_outliers` function to find the following outliers:
- Symbols that pass the null hypothesis with a p-value less than `pvalue_threshold`.
- Symbols that with a KS value above `ks_threshold`.

In [99]:
def find_outliers(ks_values, p_values, ks_threshold, pvalue_threshold=0.05):
    """
    Find outlying symbols using KS values and P-values
    
    Parameters
    ----------
    ks_values : Pandas Series
        KS static for all the tickers
    p_values : Pandas Series
        P value for all the tickers
    ks_threshold : float
        The threshold for the KS statistic
    pvalue_threshold : float
        The threshold for the p-value
    
    Returns
    -------
    outliers : set of str
        Symbols that are outliers
    """
    #TODO: Implement function
    outliers = p_values[p_values < pvalue_threshold].index
    return set(outliers)


project_tests.test_find_outliers(find_outliers)

Tests Passed


### View Data
Using the `find_outliers` function you implemented, let's see what we found.

In [100]:
ks_threshold = 0.8
outliers_5 = find_outliers(ks_values_5, p_values_5, ks_threshold)
outliers_10 = find_outliers(ks_values_10, p_values_10, ks_threshold)
outliers_20 = find_outliers(ks_values_20, p_values_20, ks_threshold)

outlier_tickers = outliers_5.union(outliers_10).union(outliers_20)
print('{} Outliers Found:\n{}'.format(len(outlier_tickers), ', '.join(list(outlier_tickers))))

299 Outliers Found:
INTU, HAS, PX, NLSN, MTB, PULCHE, NWSA, TXN, XYL, BEN, ITW, CLX, VAR, SJM, FE, VNO, LMT, CAH, PSA, HCA, AIZ, LB, CB, GREIGI, ALTAIC, DUK, PBCT, RSG, V, VTR, LEG, ALXN, MCD, MDLZ, ESS, USB, IRM, LNC, SYY, K, PNR, KO, DASYST, DGX, AME, AVB, REG, FBHS, CMI, QRVO, HRS, LVLT, EXPE, KAUFMA, GWW, PPL, AEE, HOLX, TDG, CRM, XL, EMR, NSC, APH, WU, CAT, PEG, DG, CMS, CAG, BAKERI, CA, PLD, SWK, PKG, ROP, AAP, MDT, JBHT, WAT, ICE, CCI, TEL, MS, CPB, ECL, SNA, AIG, WY, LH, PFE, SCG, VRTX, VZ, ARMENA, CVS, BDX, AMD, PNC, SYK, SRE, BXP, KLAC, DTE, SYLVES, STZ, CME, PG, TSS, COST, AZO, HRL, IVZ, CI, VVEDEN, KMX, CHD, DISCA, BAX, NKE, GIS, PEP, ADS, NWL, ED, MSI, RJF, EL, KOLPAK, HST, SBUX, CL, AMGN, TARDA, UHS, CTAS, MCO, FCX, CNC, EFX, MO, BIFLOR, NI, JPM, AIV, ORLY, AGENEN, JNJ, ROK, SO, L, GE, TMO, CHK, ALLE, SRCL, CBOE, HON, DIS, GPC, OXY, WFC, HD, PGR, UDR, CINF, UNH, MKC, SAXATI, INCY, ISRG, DE, GM, GLW, ABBV, XOM, AON, WMT, MRK, AOS, PCAR, ANSS, ALL, PHM, MCHP, MON, SNI, GESN

### Show Significance without Outliers
Let's compare the 5, 10, and 20 day signals returns without outliers to normal distributions. Also, let's see how the P-Value has changed with the outliers removed.

In [101]:
good_tickers = list(set(close.columns) - outlier_tickers)

project_helper.plot_signal_to_normal_histograms(
    [signal_return_5[good_tickers], signal_return_10[good_tickers], signal_return_20[good_tickers]],
    'Signal Return Without Outliers',
    ('5 Days', '10 Days', '20 Days'))

That's more like it! The returns are closer to a normal distribution. You have finished the research phase of a Breakout Strategy. You can now submit your project.
## Submission
Now that you're done with the project, it's time to submit it. Click the submit button in the bottom right. One of our reviewers will give you feedback on your project with a pass or not passed grade. You can continue to the next section while you wait for feedback.